# NBA DATA VISUALIZATION

In [30]:
import pandas as pd
import numpy as np

from bokeh.io import output_file, output_notebook
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource, CDSView, GroupFilter, NumeralTickFormatter
from bokeh.layouts import row, column, gridplot
from bokeh.models.widgets import Tabs, Panel

player_stats = pd.read_csv('2017-18_playerBoxScore.csv', parse_dates=['gmDate'])
team_stats = pd.read_csv('2017-18_teamBoxScore.csv', parse_dates=['gmDate'])
standings = pd.read_csv('2017-18_standings.csv', parse_dates=['stDate'])

In [31]:
west_top2 = (standings[(standings['teamAbbr'] == 'HOU') | (standings['teamAbbr'] == 'GS')]
            .loc[: , ['stDate', 'teamAbbr', 'gameWon']]
            .sort_values(['teamAbbr', 'stDate']))
west_top2.head()

stDate teamAbbr  gameWon
9   2017-10-17       GS        0
39  2017-10-18       GS        0
69  2017-10-19       GS        0
99  2017-10-20       GS        1
129 2017-10-21       GS        1

In [32]:
output_notebook()

rockets_data = west_top2[west_top2['teamAbbr'] == 'HOU']
warriors_data = west_top2[west_top2['teamAbbr'] == 'GS']

rockets_cds = ColumnDataSource(rockets_data)
warriors_cds = ColumnDataSource(warriors_data)

west_fig = figure(x_axis_type='datetime',
            plot_height=300, plot_width=600,
            title='Western conference top 2 teams wins race, 2017-2018',
            x_axis_label='Date', y_axis_label='Wins',
            toolbar_location=None)

west_fig.step('stDate', 'gameWon',
        color="#006BB6", legend_label='Warriors',
        source=warriors_cds)

west_fig.step('stDate', 'gameWon',
        color="#CE1141", legend_label='Rockets',
        source=rockets_cds)

west_fig.legend.location = 'top_left'

show(west_fig)

Loading BokehJS ...

In [33]:
output_notebook()

standings_cds = ColumnDataSource(standings)

celtics_view = CDSView(source=standings_cds,
                       filters=[GroupFilter(column_name='teamAbbr', group='BOS')])

raptors_view = CDSView(source = standings_cds,
                      filters=[GroupFilter(column_name='teamAbbr', group='TOR')])

east_fig = figure(x_axis_type='datetime',
                 plot_height=300, plot_width=600,
                 title='Eastern conference top 2 teams wins race 2017-18',
                 x_axis_label = 'date', y_axis_label='wins',
                 toolbar_location=None)

east_fig.step('stDate', 'gameWon',
             color='#007A33', legend_label='Celtics',
             source=standings_cds, view=celtics_view)

east_fig.step('stDate', 'gameWon',
             color="#CE1141", legend_label='Raptors',
             source=standings_cds, view=raptors_view)

east_fig.legend.location = 'top_left'

show(east_fig)

Loading BokehJS ...

In [34]:
show(column(west_fig, east_fig))

In [35]:
output_notebook()

east_fig.plot_width = west_fig.plot_width = 300

east_fig.title.text = "Eastern conference"
west_fig.title.text = "Western conference"

east_west_gridplot = gridplot([[west_fig, None],[None, east_fig]],
                             toolbar_location="right")

show(east_west_gridplot)

Loading BokehJS ...

In [36]:
east_fig.plot_width = west_fig.plot_width = 800

east_panel = Panel(child=east_fig, title="Eastern Conference")
west_panel = Panel(child=west_fig, title="Western Conference")

tabs = Tabs(tabs=[west_panel, east_panel])
show(tabs)

In [37]:
three_takers = player_stats[player_stats['play3PA'] > 0]

three_takers['name'] = [f'{p["playFNm"]} {p["playLNm"]}'
                       for _, p in three_takers.iterrows()]

three_takers = (three_takers.groupby('name')
               .sum()
               .loc[:, ['play3PA', 'play3PM']]
               .sort_values('play3PA', ascending=False))

three_takers = three_takers[three_takers['play3PA'] >= 100].reset_index()

three_takers['pct3PM'] = three_takers['play3PM'] / three_takers['play3PA']

three_takers.sample(5)

<ipython-input-37-c854ae75040d>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  three_takers['name'] = [f'{p["playFNm"]} {p["playLNm"]}'


name  play3PA  play3PM    pct3PM
109    Dillon Brooks      264       94  0.356061
144  Darren Collison      205       96  0.468293
80   Jordan Clarkson      318      112  0.352201
114   Ersan Ilyasova      253       91  0.359684
88      Goran Dragić      300      111  0.370000

In [39]:
output_notebook()

three_takers_cds = ColumnDataSource(three_takers)

select_tools = ["box_select", "lasso_select", "poly_select", "tap", "reset"]

fig = figure(plot_height=400,
            plot_width = 600,
            x_axis_label="Three-point shots attempted",
            y_axis_label="Percentage Made",
            title="3 PTS shots attempted vs Percentage made (min. 100 3PA), 2017-18",
            toolbar_location = "below",
            tools=select_tools)

fig.yaxis[0].formatter = NumeralTickFormatter(format='00.0%')

fig.square(x="play3PA",
          y="pct3PM",
          source=three_takers_cds,
          color="royalblue",
          selection_color="deepskyblue",
          nonselection_color="lightgray",
          nonselection_alpha=0.3)

show(fig)

Loading BokehJS ...